![Logo 1](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech1.jpg)
<div class="alert alert-block alert-info">
<h1> Komputerowe wspomaganie tłumaczenia </h1>
<h2> 6,7. <i>Preprocessing i postprocessing</i> [laboratoria]</h2> 
<h3>Rafał Jaworski (2021)</h3>
</div>

![Logo 2](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech2.jpg)

Na dzisiejszych zajęciach zajmiemy się niezwykle przydatnymi narzędziami wspomagającymi pracę tłumacza. W odróżnieniu od dotychczas poznanych, nie są one oparte na pamięci tłumaczeń, ani na słownikach. Chodzi o techniki preprocessingu i postprocessingu.

Proces tłumaczenia przeprowadzony w pełni profesjonalnie składa się z wielu faz, które angażują nie tylko tłumaczy, ale także kierowników projektu, analityków, czy korektorów. Każda z tych osób do swojej pracy może wykorzystywać system informatyczny, do którego na początku całego procesu trafiają pliki do tłumaczenia. Oznacza to, że zanim tekst źródłowy trafi do tłumacza, system ma jeszcze szansę coś w nim zmienić. A kiedy tłumacz wykona już swoją pracę, można uruchomić kolejny mechanizm, który zmodyfikuje tłumaczenie przed oddaniem go do zamawiającego. Jak się domyślamy, modyfikacje tekstu przed przekazaniem go do tłumacza nazywamy **preprocessingiem**, natomiast te dokonywane po wykonaniu tłumaczenia (ale przed zwróceniem go do klienta) nazywamy **postprocessingiem**. Terminy te, będące mało zgrabnymi kalkami z języka angielskiego, mają wersje prawdziwie polskie: przetwarzanie wstępne i końcowe. Wersje te są jednak stosowane na tyle rzadko, że mogą jedynie wprowadzić zamieszanie (co w gruncie rzeczy jest dość smutne).

Typowe operacje w fazie preprocessingu obejmują:
* identyfikację tagów xmlowych (które często są później wyświetlane w interfejsie CAT-a jako jeden niepodzielny znak)
* identyfikację segmentów, których nie należy tłumaczyć (na przykład składających się z samych liczb)

* identyfikację dat i jednostek miary w tekście źródłowym

We wszystkich tych operacjach niezwykle przydatne okazują się wyrażenia regularne.

### Ćwiczenie 1: Używając wyrażeń regularnych napisz funkcję do znajdowania wszystkich tagów XML w tekście. Funkcja powinna zwracać pozycje, na których znalazła tagi.

In [7]:
import re

def find_tags(text):
    tags = re.finditer(r'<[^>]+>', text)
    return [tag.span() for tag in tags]

# Test the function
text = 'This is a <b>bold</b> text'
find_tags(text)

[(10, 13), (17, 21)]

In [8]:
text[10:13], text[17:21]

('<b>', '</b>')

### Ćwiczenie 2: Używając wyrażeń regularnych napisz funkcję do identyfikacji segmentów, których nie należy tłumaczyć. Zastosuj wymyślone przez siebie kryteria. Funkcja is_translatable powinna zwracać True, jeśli segment powinien być przetłumaczony przez tłumacza (zwykłe zdanie). False powinno być zwrócone, kiedy segment jest nieprzetłumaczalny i powinien zostać skopiowany (np. 4.2.1.)

In [9]:
def is_translatable(text):
    # Text is translatable if it contains only letters, spaces, and punctuation
    return re.fullmatch(r'[a-zA-Z .,!?]+', text) is not None

# Test the function
is_translatable('Hello, world!'), is_translatable('Hello, 123!'), is_translatable('你好，世界！')

(True, False, False)

### Ćwiczenie 3: Używając wyrażeń regularnych napisz funkcję do identyfikacji i interpretacji 5 wybranych przez siebie formatów daty. Funkcja powinna zwracać pozycje, na których odnalazła daty oraz dzień, miesiąc i rok, które ta data reprezentuje.

In [12]:
def find_dates(text):
    # Find all dates in 5 formats: yyyy-mm-dd, yyyy/mm/dd, dd-mm-yyyy, dd/mm/yyyy, dd month yyyy
    # yyyy-mm-dd
    dates = [date.span() for date in re.finditer(r'\b\d{4}-\d{2}-\d{2}\b', text)]
    # yyyy/mm/dd
    dates = dates + [date.span() for date in re.finditer(r'\b\d{4}/\d{2}/\d{2}\b', text)]
    # dd-mm-yyyy
    dates = dates + [date.span() for date in re.finditer(r'\b\d{2}-\d{2}-\d{4}\b', text)]
    # dd/mm/yyyy
    dates = dates + [date.span() for date in re.finditer(r'\b\d{2}/\d{2}/\d{4}\b', text)]
    # dd month yyyy
    dates = dates + [date.span() for date in re.finditer(r'\b\d{2} [a-zA-Z]+ \d{4}\b', text)]
    return dates

# Test the function
text = 'The date is 2020-01-01, not 2020/01/01 or 01-01-2020 or 01/01/2020 or 01 January 2020'
find_dates(text)

[(12, 22), (28, 38), (42, 52), (56, 66), (70, 85)]

In [13]:
print(text[12:22])
print(text[28:38])
print(text[42:52])
print(text[56:66])
print(text[70:85])

2020-01-01
2020/01/01
01-01-2020
01/01/2020
01 January 2020


Po preprocessingu i tłumaczeniu czas na postprocessing. Ponieważ wykonywany jest on na przetłumaczonym tekście, jego głównym zadaniem jest eliminacja błędów popełnionych przez tłumacza w fazie tłumaczenia. Podczas postprocessingu najczęściej wykonuje się:
* korektę pisowni dla języka docelowego
* usuwanie błędów typograficznych z tekstu (np. wielokrotne spacje, brak spacji po przecinku)
Stanowi to bardzo ważne wsparcie dla edytorów i korektorów, czyli osób sprawdzających pracę tłumacza.

Jednak nowoczesne CAT-y potrafią coś jeszcze. Są w stanie w sprytny sposób wykorzystać kombinację pre- i postprocessingu do wyręczenia tłumacza w żmudnych i technicznych czynnościach. Wykonajmy następujące ćwiczenie:

### Ćwiczenie 4: Wykorzystując funkcję find_dates napisz funkcję do obsługi dat w tłumaczeniu. Wejściem jest segment źródłowy oraz docelowy, które zawierają daty, przy czym daty te mogą być w różnych formatach. Dodatkowym parametrem wejściowym jest nazwa oczekiwanego formatu daty w tłumaczeniu (np. "Europe", "US", "digit-dot". Funkcja najpierw sprawdza, czy liczba dat w tłumaczeniu zgadza się z liczbą dat w segmencie źródłowym oraz czy odpowiadające sobie daty wskazują na ten sam dzień. Jeśli nie, wypisywane jest stosowne ostrzeżenie. Oczekiwanym wyjściem jest segment docelowy, w którym wszystkie daty są w żądanym formacie. 

In [37]:
text = 'The date is 2020-01-02, not 2020/01/02 or 02-01-2020 or 02/01/2020 or 02 January 2020'

In [38]:
from dateutil.parser import parse

def change_data_to_US_format(text):
    dates = find_dates(text)

    for start, end in dates:
        date = text[start:end]
        try:
            new_date = parse(date).strftime('%m/%d/%Y')
            text = text[:start] + new_date + text[end:]
        except:
            pass
    return text

# Test the function
change_data_to_US_format(text)

'The date is 01/02/2020, not 01/02/2020 or 02/01/2020 or 02/01/2020 or 01/02/2020'

In [39]:
from dateutil.parser import parse

def change_data_to_EU_format(text):
    dates = find_dates(text)

    for start, end in dates:
        date = text[start:end]
        try:
            new_date = parse(date).strftime('%d/%m/%Y')
            text = text[:start] + new_date + text[end:]
        except:
            pass
    return text

# Test the function
change_data_to_EU_format(text)

'The date is 02/01/2020, not 02/01/2020 or 01/02/2020 or 01/02/2020 or 02/01/2020'

In [41]:
from dateutil.parser import parse

def change_data_to_digit_dot_format(text):
    dates = find_dates(text)

    for start, end in dates:
        date = text[start:end]
        try:
            new_date = parse(date).strftime('%Y.%m.%d')
            text = text[:start] + new_date + text[end:]
        except:
            pass
    return text

# Test the function
change_data_to_digit_dot_format(text)

'The date is 2020.01.02, not 2020.01.02 or 2020.02.01 or 2020.02.01 or 2020.01.02'

In [45]:
def correct_dates(source_segment, target_segment, date_format):
    # Check if number of dates in source and target segments are the same
    assert len(find_dates(source_segment)) == len(find_dates(target_segment))

    # Check if all dates are the same (ignore the format)
    source_dates = find_dates(source_segment)
    target_dates = find_dates(target_segment)
    for source_date, target_date in zip(source_dates, target_dates):
        assert change_data_to_US_format(source_segment[source_date[0]:source_date[1]]) == change_data_to_US_format(target_segment[target_date[0]:target_date[1]]), f"Dates are different: {source_segment[source_date[0]:source_date[1]]} and {target_segment[target_date[0]:target_date[1]]}"

    # Change the format of dates in the target segment
    if date_format == 'US':
        target_segment = change_data_to_US_format(target_segment)
    elif date_format == 'EU':
        target_segment = change_data_to_EU_format(target_segment)
    elif date_format == 'digit.dot':
        target_segment = change_data_to_digit_dot_format(target_segment)

    return target_segment

# Test the function
source_segment = 'The date is 2020-01-01, not 2020/01/01 or 01-01-2020 or 01/01/2020'
target_segment = "Data jest 01/01/2020, a nie 2020-01-01 lub 01-01-2020 lub 01/01/2020"
correct_dates(source_segment, target_segment, 'US')

'Data jest 01/01/2020, a nie 01/01/2020 lub 01/01/2020 lub 01/01/2020'

Co jeszcze można zrobić? Zajmijmy się tagami XML. Z punktu widzenia tłumacza najlepiej byłoby, gdyby mógł przetłumaczyć segment źródłowy zawierający tagi XML na język docelowy zupełnie ignorując te tagi. Ponieważ jednak tagi muszą jakoś znaleźć się w segmencie docelowym, przydałaby się jakaś "magiczna różdżka", która przeniosłaby wszystkie tagi ze źródła do tłumaczenia na mniej więcej dobre miejsca. Spełnijmy marzenie tłumacza!

Rozważmy następujący algorytm: na wejściu mamy segment źródłowy zawierający tagi oraz segment docelowy bez tagów. Dokonujemy tokenizacji segmentu źródłowego tak, aby tagi były osobnymi tokenami. Następnie przeprowadźmy tokenizację segmentu docelowego. Gdy to jest gotowe, możemy zabrać się za przenoszenie (kopiowanie) tagów z segmentu źródłowego do docelowego.

![Transfer tagów](img/tagtransfer.png)

Gdzie w segmencie docelowym powinien trafić tag? Przede wszystkim pomiędzy tokeny - nie chcemy rozbijać słów tagami. Pytanie tylko, pomiędzy które tokeny? Jeśli sytuacja jest taka, jak powyżej, kiedy segment źródłowy i docelowy mają taką samą liczbę słów nie będących tagami, przenosimy tagi na odpowiadające pozycje w tłumaczeniu. Natomiast jeśli długość tłumaczenia jest inna niż źródła, należy obliczać te pozycje w sposób proporcjonalny - jeśli np. mamy tag w źródle na pozycji 3, a tłumaczenie jest dwa razy dłuższe niż źródło, tag powinien być przeniesiony do tłumaczenia na pozycję 6. W przypadku niecałkowitych wartości proporcji stosujemy zaokrąglenia.

### Ćwiczenie 5: Zaimplementuj opisany algorytm transferu tagów.

In [60]:
import math

def transfer_tags(source_segment, target_segment):
    # Split the segments into tokens
    source_tokens = source_segment.split()
    target_tokens = target_segment.split()

    # Calculate the ratio of the number of tokens in the target to the number of tokens in the source
    ratio = len(target_tokens) / len(source_tokens)

    # Assign tags to tokens in the target tokens - if the source token has a tag, assign it to the corresponding token in the target tokens
    for i, source_token in enumerate(source_tokens):
        if re.match(r'<[^>]+>', source_token):
            target_index = math.ceil(i * ratio)

            if target_index >= len(target_tokens):
                target_index = len(target_tokens) - 1

            # Assign start tag
            target_tokens[target_index] = re.findall(r'<[^>]+>', source_token)[0] + target_tokens[target_index]

            # Assign end tag
            target_tokens[target_index] = target_tokens[target_index] + re.findall(r'</[^>]+>', source_token)[0]

    return ' '.join(target_tokens)

In [61]:
# Test the function (same number of tokens)
source_segment = 'This is <b>bold</b> text'
target_segment = 'To jest ważny tekst'
transfer_tags(source_segment, target_segment)

'To jest <b>ważny</b> tekst'

In [62]:
# Test the function (different number of tokens)
source_segment = 'This is <b>bold</b> text'
target_segment = 'To jest bardzo ważny tekst'
transfer_tags(source_segment, target_segment)

'To jest bardzo <b>ważny</b> tekst'